In [87]:
import pandas as pd
import numpy as np
from PIL import Image, ImageDraw
import io

from sklearn.ensemble import AdaBoostClassifier, RandomForestClassifier, GradientBoostingClassifier, ExtraTreesClassifier
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier, export_graphviz, ExtraTreeClassifier
from sklearn.utils import shuffle
import graphviz

import time
import matplotlib.pyplot as plt
import folium

In [20]:
df = pd.read_json('focused_metadata.json').reset_index()

In [21]:
df = df.drop(columns=['level_0'])

In [22]:
df.head(1)

index user_identifier                   date  longitude   latitude  \
0  10000979206    66172503@N00  2013-09-30 00:26:09.0  14.499968  46.053249   

  camera         license_name  \
0   None  Attribution License   

                                       json_autotags  tag_cluster  \
0  [[abstract, 0.809], [architecture, 0.903], [br...            1   

  external_upload  
0       instagram

In [23]:
df.columns

Index(['index', 'user_identifier', 'date', 'longitude', 'latitude', 'camera',
       'license_name', 'json_autotags', 'tag_cluster', 'external_upload'],
      dtype='object')

In [24]:
df = df[(df['date'] >= '1826-02-01 00:00:00.0') & (df['date'] <= '2020-01-01 00:00:00.0')]

In [25]:
df = df.drop(columns = ['index', 'user_identifier', 'json_autotags', 'license_name',
                        'external_upload', 'camera'])

In [26]:
df.head(1)

date  longitude   latitude  tag_cluster
0  2013-09-30 00:26:09.0  14.499968  46.053249            1

In [27]:
df['date'] = df['date'].astype('datetime64')

In [28]:
years = []
for ind, item in df['date'].iteritems():
    years.append(item.year)

In [29]:
df['year'] = years

In [30]:
df = df.drop(columns = 'date')

In [15]:
df = df.drop(columns = ['tag_cluster', 'camera'])

In [31]:
len(df)

1027392

In [32]:
len(df.dropna())

191962

In [33]:
X = df.dropna().drop(columns = 'tag_cluster')
y = df.dropna()['tag_cluster']

In [60]:
adaboost = AdaBoostClassifier()

In [61]:
adaboost.fit(X, y)

AdaBoostClassifier(algorithm='SAMME.R', base_estimator=None,
          learning_rate=1.0, n_estimators=50, random_state=None)

In [73]:
decision = adaboost.decision_function(X)

In [74]:
decision.shape

(191962, 5)

In [75]:
decision[0]

array([ 0.06794236,  0.10853943,  0.08461364, -0.12527687, -0.13581856])

In [79]:
adaboost.estimator_errors_

array([0.60698993, 0.77029389, 0.77259258, 0.79056977, 0.79793736,
       0.79748641, 0.79234628, 0.78959367, 0.78550299, 0.7971049 ,
       0.79363324, 0.78797032, 0.79703109, 0.79791654, 0.78946944,
       0.79362798, 0.79276283, 0.79572712, 0.79408467, 0.79655096,
       0.79122209, 0.79146245, 0.79317408, 0.79121328, 0.79896834,
       0.79227157, 0.79852675, 0.79534097, 0.79481537, 0.79471774,
       0.7929247 , 0.79597182, 0.7947006 , 0.79568421, 0.79513943,
       0.79578539, 0.79571145, 0.79384068, 0.7962525 , 0.79978378,
       0.79711316, 0.79576264, 0.79608612, 0.7974525 , 0.79630674,
       0.79534591, 0.79467764, 0.7950351 , 0.79642773, 0.79979678])

In [82]:
adaboost.feature_importances_

array([0.36, 0.34, 0.  , 0.02, 0.  , 0.  , 0.02, 0.02, 0.02, 0.  , 0.  ,
       0.  , 0.02, 0.  , 0.  , 0.02, 0.  , 0.  , 0.02, 0.02, 0.02, 0.12])

In [158]:
subset = df[['year', 'longitude', 'latitude', 'tag_cluster']]
subset = subset.dropna()

In [159]:
X = subset.drop(columns = 'tag_cluster')
y = subset['tag_cluster']

In [42]:
# Result obtained with chance
y.value_counts().sort_values(ascending = False).values[0] / len(y)

0.3837165689042623

In [160]:
X, y = shuffle(X, y, random_state=95)

In [161]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [204]:
rfc = RandomForestClassifier(n_estimators=1000, max_depth=22, random_state=19)
rfc.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=22, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=1000, n_jobs=None,
            oob_score=False, random_state=19, verbose=0, warm_start=False)

In [205]:
rfc.feature_importances_

array([0.03247079, 0.48370241, 0.4838268 ])

In [206]:
rfc.score(X_test, y_test)

0.5341077800640742

In [216]:
ada = AdaBoostClassifier(DecisionTreeClassifier(max_depth=22), n_estimators = 100)
ada.fit(X_train, y_train)

AdaBoostClassifier(algorithm='SAMME.R',
          base_estimator=DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=22,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best'),
          learning_rate=1.0, n_estimators=100, random_state=None)

In [217]:
ada.feature_importances_

/anaconda3/lib/python3.6/site-packages/sklearn/tree/tree.py:512: RuntimeWarning: invalid value encountered in true_divide
  return self.tree_.compute_feature_importances()


array([nan, nan, nan])

In [218]:
ada.score(X_test, y_test)

0.507957179694215

In [46]:
gbc = GradientBoostingClassifier(max_depth = 16, n_estimators = 100)
gbc.fit(X_train, y_train)

GradientBoostingClassifier(criterion='friedman_mse', init=None,
              learning_rate=0.1, loss='deviance', max_depth=10,
              max_features=None, max_leaf_nodes=None,
              min_impurity_decrease=0.0, min_impurity_split=None,
              min_samples_leaf=1, min_samples_split=2,
              min_weight_fraction_leaf=0.0, n_estimators=10,
              n_iter_no_change=None, presort='auto', random_state=None,
              subsample=1.0, tol=0.0001, validation_fraction=0.1,
              verbose=0, warm_start=False)

In [47]:
gbc.feature_importances_

array([0.51423185, 0.48576815])

In [48]:
gbc.score(X_test, y_test)

0.5056130023702238

In [50]:
gbc = GradientBoostingClassifier(max_depth = 16, n_estimators = 10)
gbc.fit(X_train, y_train)

depth: 16 . score: 0.5318156955695048
depth: 17 . score: 0.5310343031281745


KeyboardInterrupt: 

In [207]:
xtc = ExtraTreesClassifier(n_estimators=1000, max_depth=30, random_state=19)
xtc.fit(X_train, y_train)

ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=30, max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=1000, n_jobs=None,
           oob_score=False, random_state=19, verbose=0, warm_start=False)

In [ ]:
depth: 15 score: 0.5306175604927982
depth: 20 score: 0.5262678092360586

In [208]:
xtc.feature_importances_

array([0.06962724, 0.46359935, 0.46677341])

In [209]:
xtc.score(X_test, y_test)

0.5330659234756335

In [244]:
dtc = DecisionTreeClassifier(max_depth = 18, random_state=19)
dtc.fit(X_train, y_train)
dtc.score(X_test, y_test)

0.5030083608991223

In [28]:
#dtc = DecisionTreeClassifier(max_depth = 18, random_state=19)
dtc = DecisionTreeClassifier(max_depth = 12, random_state=19)
dtc.fit(X, y)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=12,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=19,
            splitter='best')

In [52]:
#dtc = DecisionTreeClassifier(max_depth = 18, random_state=19)
dtc = DecisionTreeClassifier(max_depth = 18, random_state=19)
dtc.fit(X_train, y_train)
dtc.score(X_test, y_test)

0.5030083608991223

In [66]:
dtc = DecisionTreeClassifier(max_depth = 18, random_state=19)
dtc.fit(X, y)
decision_matrix = dtc.decision_path(X)

In [70]:
decision_matrix = decision_matrix.toarray()

In [85]:
print(np.sum(decision_matrix[0]))

14


In [40]:
export_graphviz(dtc, out_file='tree.dot')
dot_data = export_graphviz(dtc, out_file=None)

In [34]:
graph = graphviz.Source(dot_data) 
graph

In [43]:
rfc = RandomForestClassifier(n_estimators=250, max_depth=22, random_state=19)
rfc.fit(X, y)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=22, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=250, n_jobs=None,
            oob_score=False, random_state=19, verbose=0, warm_start=False)

## Visualize movements

In [51]:
gbc = GradientBoostingClassifier(max_depth = 16, n_estimators = 100)
gbc.fit(X, y)

GradientBoostingClassifier(criterion='friedman_mse', init=None,
              learning_rate=0.1, loss='deviance', max_depth=16,
              max_features=None, max_leaf_nodes=None,
              min_impurity_decrease=0.0, min_impurity_split=None,
              min_samples_leaf=1, min_samples_split=2,
              min_weight_fraction_leaf=0.0, n_estimators=100,
              n_iter_no_change=None, presort='auto', random_state=None,
              subsample=1.0, tol=0.0001, validation_fraction=0.1,
              verbose=0, warm_start=False)

In [106]:
latitudes = np.arange(-90, 92, 1)
longitudes = np.arange(-180, 182, 1)
print(len(latitudes)*len(longitudes))

65884


In [107]:
df_grid = {'longitude': [], 'latitude': []}
for long in longitudes:
    for lat in latitudes:
        df_grid['latitude'].append(lat)
        df_grid['longitude'].append(long)
        
df_grid = pd.DataFrame(df_grid)
len(df_grid)

65884

In [108]:
prediction = gbc.predict(df_grid)

In [104]:
colors = ['#DF8D55', # indoor, food, people
          '#AEAEAE', # urban, geometry
          '#788FDF', # landscape, sky, water
          '#F0DF3D', # light effects, circular
          '#6ACC4C'] # plants

In [98]:
folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        movement = prediction[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])]
    
        # Add colored square to the map
        folium.Polygon(locations = [(latitudes[i], longitudes[j]),
                                   (latitudes[i+1], longitudes[j]),
                                   (latitudes[i+1], longitudes[j+1]),
                                   (latitudes[i], longitudes[j+1])],
                       color = colors[movement],
                       opacity = 1,
                       weight = 0.,
                       fill = True).add_to(folium_map)
    
#folium_map

In [99]:
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movements_map.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [125]:
proba = gbc.predict_proba(df_grid)

In [126]:
proba

array([[0.01290868, 0.27141718, 0.06747447, 0.20167138, 0.44652829],
       [0.01290868, 0.27141718, 0.06747447, 0.20167138, 0.44652829],
       [0.01290868, 0.27141718, 0.06747447, 0.20167138, 0.44652829],
       ...,
       [0.97524141, 0.01329626, 0.00665716, 0.00224886, 0.00255632],
       [0.97524141, 0.01329626, 0.00665716, 0.00224886, 0.00255632],
       [0.97524141, 0.01329626, 0.00665716, 0.00224886, 0.00255632]])

In [120]:
mvt = 0

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")



for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.Polygon(locations = [(latitudes[i], longitudes[j]),
                                   (latitudes[i+1], longitudes[j]),
                                   (latitudes[i+1], longitudes[j+1]),
                                   (latitudes[i], longitudes[j+1])],
                       color = colors[mvt],
                       opacity = probability,
                       weight = 0.,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [136]:
mvt = 0

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.CircleMarker(location = (latitudes[i], longitudes[j]),
                       color = colors[mvt],
                       opacity = np.exp(probability)/2.72,
                       weight = 0.,
                       radius = 5*probability,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [137]:
mvt = 1

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.CircleMarker(location = (latitudes[i], longitudes[j]),
                       color = colors[mvt],
                       opacity = np.exp(probability)/2.72,
                       weight = 0.,
                       radius = 5*probability,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [138]:
mvt = 2

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.CircleMarker(location = (latitudes[i], longitudes[j]),
                       color = colors[mvt],
                       opacity = np.exp(probability)/2.72,
                       weight = 0.,
                       radius = 5*probability,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [139]:
mvt = 3

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.CircleMarker(location = (latitudes[i], longitudes[j]),
                       color = colors[mvt],
                       opacity = np.exp(probability)/2.72,
                       weight = 0.,
                       radius = 5*probability,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [140]:
mvt = 4

folium_map = folium.Map(location = [30, 12],
                        zoom_start = 2,
                        tiles = "CartoDB dark_matter")

for i in range(len(latitudes)-1):
    for j in range(len(longitudes)-1):
        
        probability = proba[int(df_grid[(df_grid['latitude'] == latitudes[i]) & (
                            df_grid['longitude'] == longitudes[j])].index[0])][mvt]
    
        # Add colored square to the map
        folium.CircleMarker(location = (latitudes[i], longitudes[j]),
                       color = colors[mvt],
                       opacity = np.exp(probability)/2.72,
                       weight = 0.,
                       radius = 5*probability,
                       fill = True).add_to(folium_map)
        
# Convert the html folium map to a png image
png = folium_map._to_png(delay=40)
    
# Load the png image in order to be able to modify it
stream = io.BytesIO(png)
image = Image.open(stream)
    
# Save the png image
draw = ImageDraw.Draw(image)
image.save('movement_' + str(mvt) + '.png')

/anaconda3/lib/python3.6/site-packages/selenium/webdriver/phantomjs/webdriver.py:49: UserWarning: Selenium support for PhantomJS has been deprecated, please use headless versions of Chrome or Firefox instead
  warnings.warn('Selenium support for PhantomJS has been deprecated, please use headless '


In [155]:
len(df[df['tag_cluster'] == 4]) / len(df)

0.08499190182520401

In [147]:
len(df)

1027392

In [162]:
gbc = GradientBoostingClassifier(max_depth = 16, n_estimators = 250)
gbc.fit(X_train, y_train)
gbc.score(X_test, y_test)

0.5424165863568879

In [163]:
gbc.feature_importances_

array([0.0845494, 0.4619493, 0.4535013])